# Mount Google Drive

In [ ]:
from google.colab import data_table
data_table.enable_dataframe_formatter()

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
from google.colab import drive
drive.mount('/gdrive')

Mounted at /gdrive


# Import Experiment Data

In [ ]:
%cd /gdrive/My Drive/F3/ #REPLACE YOUR GOOGLE DRIVE DIRECTORY HERE
%ls

In [ ]:
import os
import pandas as pd

def import_test_data(folder_path):
    """
    Imports all CSV files starting with 'testdata_human' or 'testdata_LM' from the specified folder into separate DataFrames.

    Parameters:
    - folder_path (str): Path to the folder containing the CSV files.

    Returns:
    - Two DataFrames: One for files starting with 'testdata_human' and another for 'testdata_LM'.
    """
    # List all files in the specified folder
    all_files = os.listdir(folder_path)

    # Filter out files starting with 'testdata_human' or 'testdata_LM' and ending with '.csv'
    human_files = [file for file in all_files if file.startswith('testdata_human') and file.endswith('.csv')]
    lm_files = [file for file in all_files if file.startswith('testdata_LM') and file.endswith('.csv')]

    def load_files(files):
        dataframes = []
        for file in files:
            file_path = os.path.join(folder_path, file)
            df = pd.read_csv(file_path, encoding='utf-8')
            dataframes.append(df)
        return pd.concat(dataframes, ignore_index=True)

    # Load human and LM data into separate dataframes
    human_data = load_files(human_files)
    lm_data = load_files(lm_files)

    return human_data, lm_data

# Specify your folder path
path = "/content/drive/MyDrive/F3/"

# Import the data
Experiment_Data_human, Experiment_Data_LLM = import_test_data(path)
print("Human Data:")
print(Experiment_Data_human.info())
print("\nLLM Data:")
print(Experiment_Data_LLM.info())


Human Data:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3634 entries, 0 to 3633
Data columns (total 8 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   uuid            3634 non-null   object
 1   content         3634 non-null   object
 2   label           3634 non-null   object
 3   article_type    3634 non-null   object
 4   source_type     3634 non-null   object
 5   pre_post_GPT    3634 non-null   object
 6   dataset_source  3634 non-null   object
 7   text_length     3634 non-null   int64 
dtypes: int64(1), object(7)
memory usage: 227.2+ KB
None

LLM Data:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3532 entries, 0 to 3531
Data columns (total 9 columns):
 #   Column                       Non-Null Count  Dtype 
---  ------                       --------------  ----- 
 0   uuid                         3532 non-null   object
 1   ai_content                   3532 non-null   object
 2   human_content                3532 n

In [ ]:
# Add a new column "source_type" with value "LLM" for all rows
Experiment_Data_LLM["source_type"] = "LLM"

# Display the first few rows of the updated dataframe for verification
print(Experiment_Data_LLM.head())


                                   uuid  \
0  0a7790ed-3342-45fd-a8cd-f1623c9d2045   
1  0431738d-8c3d-4876-a729-9f3ac0297ae2   
2  eba8731e-366d-4d19-920d-3aaf12d50b4b   
3  8bc31383-84f4-4ea8-bd9f-775e60eaa025   
4  37a0d77d-0b06-4656-b531-60897fae7df5   

                                          ai_content  \
0  Netflix Rejects Sense8 Renewal Due to Too Many...   
1  Disney’s ‘Olaf’s Frozen Adventure’ has been ca...   
2  The new NBC show chronicling Lyle and Erik Men...   
3  Medical News Today interviewed Prof. David Hey...   
4  The coronavirus outbreak has highlighted the m...   

                                       human_content  \
0  The reason we've taken so long to get back to ...   
1  Hi everyone, he’s Olaf and he likes warm hugs ...   
2  The stars of a new NBC show chronicling Lyle a...   
3  in conversation with world health organization...   
4  all data and statistics are based on publicly ...   

                         aigenerated_content_cleaned ai_generated_l

In [ ]:
# Drop unwanted columns
Experiment_Data_LLM.drop(columns=['ai_content', 'human_content'], inplace=True)

# Rename column
Experiment_Data_LLM.rename(columns={'aigenerated_content_cleaned': 'content', 'ai_generated_label': 'label'}, inplace=True)

# Display the updated dataframe info for verification
print(Experiment_Data_LLM.info())


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3532 entries, 0 to 3531
Data columns (total 8 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   uuid            3532 non-null   object
 1   content         3532 non-null   object
 2   label           3532 non-null   object
 3   Prompt_type     3532 non-null   object
 4   pre_post_GPT    3532 non-null   object
 5   article_type    3532 non-null   object
 6   dataset_source  3532 non-null   object
 7   source_type     3532 non-null   object
dtypes: object(8)
memory usage: 220.9+ KB
None


In [ ]:
# Concatenate the two dataframes along the rows
Experiment_data = pd.concat([Experiment_Data_human, Experiment_Data_LLM], axis=0, ignore_index=True)

# Display the info of the concatenated dataframe for verification
print(Experiment_data.info())


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7166 entries, 0 to 7165
Data columns (total 9 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   uuid            7166 non-null   object 
 1   content         7166 non-null   object 
 2   label           7166 non-null   object 
 3   article_type    7166 non-null   object 
 4   source_type     7166 non-null   object 
 5   pre_post_GPT    7166 non-null   object 
 6   dataset_source  7166 non-null   object 
 7   text_length     3634 non-null   float64
 8   Prompt_type     3532 non-null   object 
dtypes: float64(1), object(8)
memory usage: 504.0+ KB
None


In [ ]:
columns_to_count = ['label', 'article_type', 'source_type', 'pre_post_GPT', 'dataset_source', 'text_length', 'Prompt_type']

for column in columns_to_count:
    print(f"Value counts for {column}:\n")
    print(Experiment_data[column].value_counts())
    print("\n" + "-"*50 + "\n")


Value counts for label:

fake    4318
real    2848
Name: label, dtype: int64

--------------------------------------------------

Value counts for article_type:

twitter post    4127
news article    3039
Name: article_type, dtype: int64

--------------------------------------------------

Value counts for source_type:

human    3634
LLM      3532
Name: source_type, dtype: int64

--------------------------------------------------

Value counts for pre_post_GPT:

pre-GPT     3693
post-GPT    3473
Name: pre_post_GPT, dtype: int64

--------------------------------------------------

Value counts for dataset_source:

x-Gen                      3811
CoAID                      2356
FakeNewsNet_Gossipcop       963
FakeNewsNet_Politifacts      36
Name: dataset_source, dtype: int64

--------------------------------------------------

Value counts for text_length:

19.0      134
20.0      131
16.0      130
15.0      128
13.0      120
         ... 
1918.0      1
1388.0      1
1436.0      1
913.0  

In [ ]:
Experiment_data

uuid  \
0     7c4db7e7-e63c-49e0-8210-0627b68112d4   
1     16d0d2c9-76a5-449f-baf9-d497d605c6b4   
2     30a3225a-2a4c-4ff6-8cc9-600388db794a   
3     62c8cd0b-852e-48ea-8c5e-b88d8172486a   
4     3e5f8506-20ac-41bf-8407-0f454b87ce76   
...                                    ...   
7161  f10c5702-98ae-44e9-928b-34d5a58713f3   
7162  308c43e4-5c35-48d6-b2d7-e1b393379d8c   
7163  51cee66a-9dec-4fb8-9ab1-9eaea7f8b39a   
7164  f034cfc2-9f2b-414c-b59a-002182baf7fa   
7165  78ef2e5f-3a67-4f60-a252-7016a0212f23   

                                                content label  article_type  \
0     Wiley Nickel supports “abortion all the way up...  fake  twitter post   
1     "Under Abbott, Texas leads the nation in rape ...  real  twitter post   
2     Kari Lake and Mark Finchem “have said that the...  real  twitter post   
3     “I’ve been against that war in Afghanistan fro...  fake  twitter post   
4     President Joe Biden withdrew troops from Afgha...  fake  twitter post   
...                                                 ...   ...           ...   
7161  summary irs will not target small businesses a...  real  twitter post   
7162  summary voter id laws have been implemented in...  real  twitter post   
7163  summary wisconsin offers free healthcare witho...  real  twitter post   
7164  rubio and desantis opposed hurricane sandy rel...  real  twitter post   
7165  summary black women have a higher risk of mate...  real  twitter post   

     source_type pre_post_GPT dataset_source  text_length Prompt_type  
0          human     post-GPT          x-Gen         19.0         NaN  
1          human     post-GPT          x-Gen         25.0         NaN  
2          human     post-GPT          x-Gen         25.0         NaN  
3          human     post-GPT          x-Gen         16.0         NaN  
4          human     post-GPT          x-Gen         27.0         NaN  
...          ...          ...            ...          ...         ...  
7161         LLM     post-GPT          x-Gen          NaN    critical  
7162         LLM     post-GPT          x-Gen          NaN    critical  
7163         LLM     post-GPT          x-Gen          NaN    critical  
7164         LLM     post-GPT          x-Gen          NaN    critical  
7165         LLM     post-GPT          x-Gen          NaN    critical  

[7166 rows x 9 columns]

In [ ]:
Experiment_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7166 entries, 0 to 7165
Data columns (total 9 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   uuid            7166 non-null   object 
 1   content         7166 non-null   object 
 2   label           7166 non-null   object 
 3   article_type    7166 non-null   object 
 4   source_type     7166 non-null   object 
 5   pre_post_GPT    7166 non-null   object 
 6   dataset_source  7166 non-null   object 
 7   text_length     3634 non-null   float64
 8   Prompt_type     3532 non-null   object 
dtypes: float64(1), object(8)
memory usage: 504.0+ KB


# Classification Prompt Engineering

## Cloze Prompt

In [ ]:
"""Generate a prompt using template.

  Args:
    F3 prompt template (θ) has three parameters: (1) content (C) embeds data to be analyzed. The content parameter in the the function [ai_text_generator] (2) Impersonator (R)
    establishes context, guides LLMs’ generation and detection, and overrides alignment-tuning. (3) Instructor (I)
    provides directives to guide LLM.

  Returns:
    A generated prompt.
"""
def get_prompt(prompt_type):

  impersonator = ""
  instructor = ""
  cloze_prompt = "Is this real or fake news? {_____}"

  if prompt_type == "VaN":# Technique
    impersonator = "You are an AI assistant trained to detect fake news."
    instructor = "Analyze the given text and determine if it is real or fake news."

  elif prompt_type == "A_CoT":# Technique
    impersonator = "You are an AI assistant trained to detect fake news."
    instructor = "Analyze the given text, think step-by-step, and determine if it is real or fake news."

  elif prompt_type == "X_CoT":# Technique
    impersonator = "You are an AI assistant trained to detect fake news."
    instructor = "Analyze the given text, explain your reasoning step-by-step, and determine if it is real or fake news."

  elif prompt_type == "A_Con":# Technique
    impersonator = "You are an AI assistant trained to detect fake news with confidence estimates."
    instructor = "Analyze the given text, provide a confidence score between 0-100%, and determine if it is real or fake news."

  elif prompt_type == "MSReN":# Technique
    impersonator = "You are an AI fact checker trained to detect fake news."
    instructor = "Analyze the text in detail as a fact checker would. Check for misleading info, false claims, biased language. If real, respond 'True', if fake, respond 'False'."

  elif prompt_type == "MSReN_CoT":# Technique
    impersonator = "You are an AI fact checker trained to detect fake news."
    instructor = "Analyze the text in detail as a fact checker would. Explain your reasoning step-by-step. If real, respond 'True', if fake, respond 'False'."

  elif prompt_type == "DeF_Gen":# Technique
    impersonator = "You are an AI assistant trained to detect fake news."
    instructor = "Determine if the text contains factual information supported by evidence (real) or misleading/inaccurate information (fake). Respond with 'True' or 'False'."

  elif prompt_type == "DeF_SpeC":# Technique
    impersonator = "You are an AI assistant trained to detect fake news."
    instructor = "Analyze the tone, language, sources to determine if the text is real (supported by facts) or fake (misleading info). Respond with 'True' or 'False'."

  elif prompt_type == "Analyze_Cld2":# Technique
    impersonator = "You are an AI assistant specially trained to detect fake news with high accuracy."
    instructor = """Analyze the given news article in depth. Check for the following indicators that it may be fake news:
    - Inaccurate or misleading information
    - Lack of evidence for claims
    - Emotionally charged language with intent to provoke outrage or shock
    - Biased portrayal of events or people
    - Unverified sources or 'experts'
    - Logical fallacies or conspiracy theories without proof

    If the article exhibits multiple indicators of fake news, respond 'False'. If the article is factual and supported by credible evidence, respond 'True'. Your judgement should be highly accurate.
    """

  elif prompt_type == "Analyze_AI_GPT":# Technique
    impersonator = "You are an AI trained with extensive knowledge up to 2022 on various news articles, both real and fake."
    instructor = """Analyze the given text for potential indicators of fake news, such as:
    - Sensationalist or emotionally charged language.
    - Absence of specific details or dates.
    - Over-generalizations or sweeping statements.
    - Statements that are too good to be true or overly dramatic.
    - Lack of logical flow in arguments or jumping to conclusions without evidence.

    It's essential to understand that without real-time verification capabilities, your judgment will be based on patterns and knowledge up to your last training. Using these textual cues and your training, determine the credibility of the given text. If it seems factual and consistent with your training, respond 'True'. If it exhibits patterns typical of fake news, respond 'False'."""

  prompt = f"{impersonator} {instructor} {cloze_prompt}"

  return prompt

# Experiment

## DeepInfra


We using [DeepInfra](https://deepinfra.com/) API for inference with the following LLMs.


1.   LLaMa-2: meta-llama/Llama-2-70b-chat-hf
2.   Dolly-2: databricks/dolly-v2-12b
3.   Falcon: tiiuae/falcon-40b-q51
4.   LLaMa-2-GPT: jondurbin/airoboros-l2-70b-gpt4-1.4.1



### Llama-2 70b, Dolly-2, LLaMA-GPT-4

In [ ]:
# %pip install openai

In [ ]:
# from time import sleep
# import openai
# import os
# import pandas as pd
# import openai
# from tqdm import tqdm
# import concurrent.futures

# # Set DeepInfra token
# openai.api_key = "xxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxx"
# openai.api_base = "https://api.deepinfra.com/v1/openai"

In [ ]:
# import multiprocessing

# cores = multiprocessing.cpu_count() # Count the number of cores in a computer
# cores

In [ ]:
import os
import pandas as pd
import openai
from tqdm import tqdm
import concurrent.futures

# Set the prompt pattern
prompt_types = ["VaN", "A_CoT", "X_CoT", "A_Con", "MSReN", "MSReN_CoT", "DeF_Gen", "DeF_SpeC", "Analyze_Cld2", "Analyze_AI_GPT"]

# Ensure backup directory exists
backup_folder = "llama2_GPT"
os.makedirs(backup_folder, exist_ok=True)

# Load previous progress if exists
backup_path = os.path.join(backup_folder, "progress.csv")
last_processed_uuid = None
last_processed_prompt = None

try:
    progress_df = pd.read_csv(backup_path)
    last_processed_uuid = progress_df.iloc[-1]['uuid']
    last_processed_prompt = progress_df.iloc[-1]['Prompt_type']
except FileNotFoundError:
    progress_df = pd.DataFrame(columns=['uuid', 'Llama2-label', 'content', 'label', 'Prompt_type', 'pre_post_GPT', 'article_type', 'dataset_source', 'source_type'])

# Create a list of all combinations of rows and prompt types
if last_processed_uuid and last_processed_prompt:
    start_idx = Experiment_data[Experiment_data['uuid'] == last_processed_uuid].index[0]
    start_prompt_idx = prompt_types.index(last_processed_prompt) + 1
    if start_prompt_idx >= len(prompt_types):
        start_idx += 1
        start_prompt_idx = 0

    all_data = [(row, prompt) for _, row in Experiment_data.iloc[start_idx:].iterrows() for prompt in (prompt_types[start_prompt_idx:] if row['uuid'] == last_processed_uuid else prompt_types)]
else:
    all_data = [(row, prompt) for _, row in Experiment_data.iterrows() for prompt in prompt_types]

# Function to process each row for a given prompt type
def process_row_for_prompt(data):
    row, prompt_type = data
    content = row['content']
    cloze_prompt = get_prompt(prompt_type)
    prompt_content = f"Content: '{content}' prompt: '{cloze_prompt}. Please state a single probable answer if you are uncertain, lack evidence or unverified, but please answer with your single word: 'True' or 'False'. {______}'"
    try:
        chat_completion = openai.ChatCompletion.create(
            """
              Replace the model name below with:
              1.   LLaMa-2: meta-llama/Llama-2-70b-chat-hf
              2.   Dolly-2: databricks/dolly-v2-12b
              3.   LLaMa-2-GPT: jondurbin/airoboros-l2-70b-gpt4-1.4.1
            """
            model="jondurbin/airoboros-l2-70b-gpt4-1.4.1",
            messages=[{"role": "user", "content": prompt_content}],
            n=1
        )
        model_output = chat_completion.choices[0].message.content.strip()
        return (row['uuid'], model_output, content, row['label'], prompt_type, row['pre_post_GPT'], row['article_type'], row['dataset_source'], row['source_type'])
    except openai.error.OpenAIError as e:
        print(f"Error for uuid {row['uuid']} with prompt {prompt_type}: {e}")
        return (row['uuid'], "Error", content, row['label'], prompt_type, row['pre_post_GPT'], row['article_type'], row['dataset_source'], row['source_type'])

# Parallelize using ThreadPoolExecutor
results = []
with concurrent.futures.ThreadPoolExecutor() as executor:
    for data in tqdm(executor.map(process_row_for_prompt, all_data), total=len(all_data)):
        results.append(data)
        # Adjust the save condition (you might want to modify this based on the frequency of saving)
        if len(results) % 10 == 0 or len(results) == len(all_data):
            print("Saving progress.")
            columns = ['uuid', 'Llama2-label', 'content', 'label', 'Prompt_type', 'pre_post_GPT', 'article_type', 'dataset_source', 'source_type']
            temp_df = pd.DataFrame(results, columns=columns)
            progress_df = pd.concat([progress_df, temp_df], axis=0, ignore_index=True)
            progress_df.to_csv(backup_path, mode='w', header=True, index=False)
            results = []


In [ ]:
%ls

Completed/  output_table.tex                    testdata_LM_article_postGPT.csv
Dolly2/     testdata_human_article_PostGPT.csv  testdata_LM_articles_preGPT.csv
Falcon2/    testdata_human_articles_preGPT.csv  testdata_LM_SM_postGPT.csv
GPT3_5T/    testdata_human_SM_PostGPT.csv       testdata_LM_SM_preGPT.csv
GPT4/       testdata_human_SM_preGPT.csv


### Falcon-40b



In [ ]:
!pip install requests

Falcon is accessible via python request package below


In [ ]:
import os
import pandas as pd
import json
import requests
from tqdm import tqdm
import concurrent.futures

# Set the prompt pattern
prompt_types = ["VaN", "A_CoT", "X_CoT", "A_Con", "MSReN", "MSReN_CoT", "DeF_Gen", "DeF_SpeC", "Analyze_Cld2", "Analyze_AI_GPT"]

# Token for authentication
DEEPINFRA_TOKEN = "xxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxx"

# Ensure backup directory exists
backup_folder = "Falcon2"
os.makedirs(backup_folder, exist_ok=True)

# Load previous progress if exists
backup_path = os.path.join(backup_folder, "progress.csv")
last_processed_uuid = None
last_processed_prompt = None

try:
    progress_df = pd.read_csv(backup_path)
    last_processed_uuid = progress_df.iloc[-1]['uuid']
    last_processed_prompt = progress_df.iloc[-1]['Prompt_type']
except FileNotFoundError:
    progress_df = pd.DataFrame(columns=['uuid', 'Falcon2-label', 'content', 'label', 'Prompt_type', 'pre_post_GPT', 'article_type', 'dataset_source', 'source_type'])

# Create a list of all combinations of rows and prompt types
# ... [existing code for this part, which wasn't provided in your snippets] ...

# Function to process each row for a given prompt type
def process_row_for_prompt(data):
    row, prompt_type = data
    content = row['content'][:2048]
    cloze_prompt = get_prompt(prompt_type)  # Assuming this function exists in your full code
    prompt_content = f"Please state a single probable answer if you are uncertain, lack evidence or unverified, but please answer with your single word: 'True' or 'False'.'  prompt: '{cloze_prompt}. Content: '{content}'"

    url = 'https://api.deepinfra.com/v1/inference/tiiuae/falcon-40b-q51' #Falcon model url
    headers = {
        'Content-Type': 'application/json',
        'Authorization': f'Bearer {DEEPINFRA_TOKEN}'
    }
    data_payload = {
        'input': {
            'prompt': prompt_content
        }
    }

    try:
        response = requests.post(url, headers=headers, json=data_payload)
        response.raise_for_status()  # Raises an HTTPError if the HTTP request returned an unsuccessful status code

        json_response = response.json()
        model_output = json_response['choices'][0]['message']['content'].strip()
        return (row['uuid'], model_output, content, row['label'], prompt_type, row['pre_post_GPT'], row['article_type'], row['dataset_source'], row['source_type'])

    except requests.RequestException as e:
        error_message = f"Error for uuid {row['uuid']} with prompt {prompt_type}: HTTP status {e}"
        if response.text:
            error_message += f", Response body: {response.text}"
        print(error_message)
        return (row['uuid'], "Error", content, row['label'], prompt_type, row['pre_post_GPT'], row['article_type'], row['dataset_source'], row['source_type'])


# Parallelize using ThreadPoolExecutor
results = []
with concurrent.futures.ThreadPoolExecutor() as executor:
    for data in tqdm(executor.map(process_row_for_prompt, all_data), total=len(all_data)):
        results.append(data)
        # Adjust the save condition (you might want to modify this based on the frequency of saving)
        if len(results) % 10 == 0 or len(results) == len(all_data):
            print("Saving progress.")
            columns = ['uuid', 'Falcon2-label', 'content', 'label', 'Prompt_type', 'pre_post_GPT', 'article_type', 'dataset_source', 'source_type']
            temp_df = pd.DataFrame(results, columns=columns)
            progress_df = pd.concat([progress_df, temp_df], axis=0, ignore_index=True)
            progress_df.to_csv(backup_path, mode='w', header=True, index=False)
            results = []


## Open AI

We using Open AIAPI for inference with the following LLMs.


1.   GPT3.5- Turbo
2.   GPT4



### GPT3.5 Turbo

In [ ]:
%pip install openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.0/77.0 kB 1.4 MB/s eta 0:00:00


In [ ]:
from time import sleep
import openai
import os
import pandas as pd
import openai
from tqdm import tqdm
import concurrent.futures

In [ ]:
api_key = "sk-xxxxxxxxxxxxxxxxxxxxxxxxxxxxx"

In [ ]:
import multiprocessing

cores = multiprocessing.cpu_count() # Count the number of cores in a computer
cores

2

In [ ]:
import os
import pandas as pd
import openai
import time
from tqdm import tqdm
import concurrent.futures

# Function for AI text classification
def ai_text_classification(prompt, content):
    openai.api_key = api_key

    while True:
        try:
            time.sleep(11)  # Sleep for 600 milliseconds
            response = openai.ChatCompletion.create(
                model="gpt-3.5-turbo",
                temperature=0.7,
                messages=[
                    {"role": "system", "content": prompt},
                    {"role": "user", "content": content[:4097]},
                ],
            )
            return response.choices[0].message.content.strip()
        except Exception as e:
            print(e)
            time.sleep(30)  # Wait for 60 seconds before retrying

# Load the prompt pattern
prompt_types = ["VaN", "A_CoT", "X_CoT", "A_Con", "MSReN", "MSReN_CoT", "DeF_Gen", "DeF_SpeC", "Analyze_Cld2", "Analyze_AI_GPT"]

# Ensure backup directory exists
backup_folder = "GPT3_5T"
os.makedirs(backup_folder, exist_ok=True)

# Load previous progress if exists
backup_path = os.path.join(backup_folder, "progress.csv")
last_processed_uuid = None
last_processed_prompt = None

try:
    progress_df = pd.read_csv(backup_path)
    last_processed_uuid = progress_df.iloc[-1]['uuid']
    last_processed_prompt = progress_df.iloc[-1]['Prompt_type']
except FileNotFoundError:
    progress_df = pd.DataFrame(columns=['uuid', 'GPT3_5T-label', 'content', 'label', 'Prompt_type', 'pre_post_GPT', 'article_type', 'dataset_source', 'source_type'])

# Create a list of all combinations of rows and prompt types
if last_processed_uuid and last_processed_prompt:
    start_idx = Experiment_data[Experiment_data['uuid'] == last_processed_uuid].index[0]
    start_prompt_idx = prompt_types.index(last_processed_prompt) + 1
    if start_prompt_idx >= len(prompt_types):
        start_idx += 1
        start_prompt_idx = 0

    all_data = [(row, prompt) for _, row in Experiment_data.iloc[start_idx:].iterrows() for prompt in (prompt_types[start_prompt_idx:] if row['uuid'] == last_processed_uuid else prompt_types)]
else:
    all_data = [(row, prompt) for _, row in Experiment_data.iterrows() for prompt in prompt_types]

# Function to process each row for a given prompt type
def process_row_for_prompt(data):
    row, prompt_type = data
    content = row['content']
    cloze_prompt = get_prompt(prompt_type)  # assuming this function exists in your full code
    prompt_content = f"Content: '{content}' prompt: '{cloze_prompt}. Please strictly state a single probable answer if you are uncertain, lack evidence or unverified, but please strictly answer with your single word: 'True' or 'False'.'"

    try:
        model_output = ai_text_classification(prompt_content, content)
        return (row['uuid'], model_output, content, row['label'], prompt_type, row['pre_post_GPT'], row['article_type'], row['dataset_source'], row['source_type'])
    except Exception as e:
        print(f"Error for uuid {row['uuid']} with prompt {prompt_type}: {str(e)}")
        return (row['uuid'], "Error", content, row['label'], prompt_type, row['pre_post_GPT'], row['article_type'], row['dataset_source'], row['source_type'])

# Parallel execution using ThreadPoolExecutor
results = []
with concurrent.futures.ThreadPoolExecutor() as executor:
    for data in tqdm(executor.map(process_row_for_prompt, all_data), total=len(all_data)):
        results.append(data)

        # Adjust the save condition (you might want to modify this based on the frequency of saving)
        if len(results) % 10 == 0 or len(results) == len(all_data):
            print("Saving progress.")
            columns = ['uuid', 'GPT3_5T-label', 'content', 'label', 'Prompt_type', 'pre_post_GPT', 'article_type', 'dataset_source', 'source_type']
            temp_df = pd.DataFrame(results, columns=columns)
            progress_df = pd.concat([progress_df, temp_df], axis=0, ignore_index=True)
            progress_df.to_csv(backup_path, mode='w', header=True, index=False)
            results = []


### GPT4

In [ ]:
%pip install openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.0/77.0 kB 1.5 MB/s eta 0:00:00


In [ ]:
from time import sleep
import openai
import os
import pandas as pd
import openai
from tqdm import tqdm
import concurrent.futures

In [ ]:
api_key = "sk-xxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxx"

In [ ]:
import multiprocessing

cores = multiprocessing.cpu_count() # Count the number of cores in a computer
cores

2

In [ ]:
import os
import pandas as pd
import openai
import time
from tqdm import tqdm

# Function for AI text classification
def ai_text_classification(prompt, content):
    openai.api_key = api_key

    while True:
        try:
            time.sleep(11)  # Sleep for 11 seconds
            response = openai.ChatCompletion.create(
                model="gpt-4",
                temperature=0.7,
                messages=[
                    {"role": "system", "content": prompt},
                    {"role": "user", "content": content[:4097]},
                ],
            )
            return response.choices[0].message.content.strip()
        except Exception as e:
            error_str = str(e)
            print(error_str)
            if "Rate limit reached" in error_str:
                wait_time = re.search(r"try again in (\d+)ms", error_str)
                if wait_time:
                    wait_time = int(wait_time.group(1))/1000  # Convert ms to seconds
                    time.sleep(wait_time + 5)  # Adding an extra 5 seconds for buffer
            else:
                time.sleep(30)

# Load the prompt pattern
prompt_types = ["VaN", "A_CoT", "X_CoT", "A_Con", "MSReN", "MSReN_CoT", "DeF_Gen", "DeF_SpeC", "Analyze_Cld2", "Analyze_AI_GPT"]

# Ensure backup directory exists
backup_folder = "GPT4"
os.makedirs(backup_folder, exist_ok=True)

# Load previous progress if exists
backup_path = os.path.join(backup_folder, "progress.csv")
last_processed_uuid = None
last_processed_prompt = None

try:
    progress_df = pd.read_csv(backup_path, encoding='latin1')
    last_processed_uuid = progress_df.iloc[-1]['uuid']
    last_processed_prompt = progress_df.iloc[-1]['Prompt_type']
except FileNotFoundError:
    progress_df = pd.DataFrame(columns=['uuid', 'GPT4-label', 'content', 'label', 'Prompt_type', 'pre_post_GPT', 'article_type', 'dataset_source', 'source_type'])

# Create a list of all combinations of rows and prompt types
if last_processed_uuid and last_processed_prompt:
    start_idx = Experiment_data[Experiment_data['uuid'] == last_processed_uuid].index[0]
    start_prompt_idx = prompt_types.index(last_processed_prompt) + 1
    if start_prompt_idx >= len(prompt_types):
        start_idx += 1
        start_prompt_idx = 0

    all_data = [(row, prompt) for _, row in Experiment_data.iloc[start_idx:].iterrows() for prompt in (prompt_types[start_prompt_idx:] if row['uuid'] == last_processed_uuid else prompt_types)]
else:
    all_data = [(row, prompt) for _, row in Experiment_data.iterrows() for prompt in prompt_types]

# Function to process each row for a given prompt type
def process_row_for_prompt(data):
    row, prompt_type = data
    content = row['content']
    cloze_prompt = get_prompt(prompt_type)  # assuming this function exists in your full code
    prompt_content = f"Content: '{content}' prompt: '{cloze_prompt}. Please strictly state a single probable answer if you are uncertain, lack evidence or unverified, but please strictly answer with your single word: 'True' or 'False'.'"

    try:
        model_output = ai_text_classification(prompt_content, content)
        return (row['uuid'], model_output, content, row['label'], prompt_type, row['pre_post_GPT'], row['article_type'], row['dataset_source'], row['source_type'])
    except Exception as e:
        print(f"Error for uuid {row['uuid']} with prompt {prompt_type}: {str(e)}")
        return (row['uuid'], "Error", content, row['label'], prompt_type, row['pre_post_GPT'], row['article_type'], row['dataset_source'], row['source_type'])

# Process each data sequentially
results = []
for data in tqdm(all_data, total=len(all_data)):
    result = process_row_for_prompt(data)
    results.append(result)

    # Adjust the save condition (you might want to modify this based on the frequency of saving)
    if len(results) % 10 == 0 or len(results) == len(all_data):
        print("Saving progress.")
        columns = ['uuid', 'GPT4-label', 'content', 'label', 'Prompt_type', 'pre_post_GPT', 'article_type', 'dataset_source', 'source_type']
        temp_df = pd.DataFrame(results, columns=columns)
        progress_df = pd.concat([progress_df, temp_df], axis=0, ignore_index=True)
        progress_df.to_csv(backup_path, mode='w', header=True, index=False)
        results = []
